In [68]:
from elasticsearch import Elasticsearch
from elasticsearch_dsl import Search,Q
from elasticsearch_dsl.query import MoreLikeThis
from datetime import timedelta, date
import pandas as pd
import json
import re
import datetime

In [69]:
es = Elasticsearch([{'host': 'localhost', 'port': 9200}])

In [3]:
def JSON_converter(final_header_lst, val_lst):
    output = {}
    for header, val in zip(final_header_lst, val_lst):
        output[header] = val
     
    return output
    #return json.dumps(output, indent = 2)

def JSON_generator(input_df):
    header_lst = input_df.columns.tolist()
    #header_lst.remove('contract_id')
    #header_lst.remove('file_name')
    final_header_lst=[]
    for header in header_lst:
        if " " in header:
            final_header_lst.append(header.replace(" ","_"))
        else:
            final_header_lst.append(header)
            
    for idx, row_val in input_df.iterrows():
        file_name = row_val[-1]
        file_path = 'data/Txt files/'+file_name
        contract_id = row_val[0]
        JSON_data = row_val[0:-1].tolist()
        try:
            with open(file_path, 'r' , encoding='utf-8') as f:
                text_data = f.read().replace('\n', '').replace(u'\xa0',' ')
            final_header_lst.append('text_content') 
            JSON_data.append(file_name)
            JSON_data.append(text_data)
            print(JSON_data)
            yield contract_id, JSON_converter(final_header_lst, JSON_data)
            
        except:
            print('cannot process txt_file {}'.format(file_name))

def process_dataSource(input_df):
    
    output_df = input_df.copy()
    output_df['Contract Duration (Days)'] = output_df['Contract Duration (Days)'].fillna('0')
    output_df['Contract Duration (Days)'] = output_df['Contract Duration (Days)'].apply(lambda x: int(re.sub('[^0-9]', '', x)))
    output_df['contract_id'] = output_df['contract_id'].astype(int)
    
    output_df['Effective Date'] = pd.to_datetime(output_df['Effective Date'], utc=True)
    output_df['Expiration Date'] = pd.to_datetime(output_df['Expiration Date'], utc=True)
    output_df['Effective Date'].fillna(datetime.datetime(2100,1,1), inplace = True)
    output_df['Expiration Date'].fillna(datetime.datetime(2100,1,1), inplace = True)
    #output_df['Effective Date'] = output_df['Effective Date'].strftime('%Y-%m-%d')
    #output_df['Expiration Date'] = output_df['Expiration Date'].strftime('%Y-%m-%d')                                                                      
    output_df.fillna('', inplace = True)
    
    return output_df

ContractMetaData = pd.read_csv('data/300_metadata.csv')
processed_data = process_dataSource(ContractMetaData)
contract_g = JSON_generator(processed_data)

In [4]:
processed_data.tail(5)

contract_id Alternate Dispute Resolution Terms Confidentiality Terms  \
299         9377                                YES                   YES   
300       111111                                YES                   YES   
301       111112                                 NO                   YES   
302       111113                                YES                   YES   
303       111114                                 NO                   YES   

     Contract Duration (Days) Data Incident Response For Data Breaches Term  \
299                         0                                            NO   
300                       250                                           YES   
301                       250                                            NO   
302                       250                                           YES   
303                       250                                            NO   

                Effective Date            Expiration Date       Governing Law  \
299        2100-01-01 00:00:00        2100-01-01 00:00:00  AffiliatesNew York   
300  2017-05-17 00:00:00+00:00  2021-12-31 00:00:00+00:00  AffiliatesNew York   
301  2017-05-17 00:00:00+00:00  2022-01-31 00:00:00+00:00  AffiliatesNew York   
302  2017-05-17 00:00:00+00:00  2022-03-01 00:00:00+00:00  AffiliatesNew York   
303  2017-05-17 00:00:00+00:00  2022-03-01 00:00:00+00:00  AffiliatesNew York   

    Indemnity Terms Jurisdiction  ...          Signer 1 Signer 1 Title  \
299             YES               ...   Stephen J. Farr      President   
300             YES               ...  Edward Jankowski                  
301             YES               ...  Edward Jankowski                  
302             YES               ...  Edward Jankowski                  
303             YES               ...  Edward Jankowski                  

          Signer 2                         Signer 2 Title Termination Days  \
299                 President and Chief Executive Officer                    
300  Michael Acton                                                    20.0   
301  Michael Acton                                                    20.0   
302  Michael Acton                                                    20.0   
303  Michael Acton                                                    20.0   

                             Termination Notice Termination Rights Terms  \
299                                                                  YES   
300  within twenty (20) days of the termination                      YES   
301  within twenty (20) days of the termination                      YES   
302  within twenty (20) days of the termination                      YES   
303  within twenty (20) days of the termination                      YES   

    Waiver Of Jury Trial Terms Warranty Terms  \
299                         NO            YES   
300                         NO            YES   
301                         NO            YES   
302                         NO            YES   
303                         NO            YES   

                                             file_name  
299  22321_ZogenixInc_20190509_10-Q_EX-10.2_1166331...  
300                                   Sample_file1.txt  
301                                   Sample_file2.txt  
302                                   Sample_file3.txt  
303                                   Sample_file4.txt  

[5 rows x 47 columns]

In [ ]:
es.indices.delete(index='k-nary', ignore=[400, 404])

In [5]:
for contract_id,json_data in contract_g:
    res = es.index(index='k-nary', body=json_data)
    print(res)

[8730, 'NO', 'YES', 0, 'NO', Timestamp('2019-11-08 00:00:00+0000', tz='UTC'), datetime.datetime(2100, 1, 1, 0, 0), 'the United States of America', 'YES', 'Texas', 'NO', 'YES', 'NO', 'business at 575 N. Dairy Ashford, Energy Center II, Suite 210, Houston, Texas 77079', 'PEDEVCO Corp.', 'and state courts located in Texas', '', '', '', '', 'Texas', 'Texas', 'Corp', '77079', '', 'Viktor Tkachev', 'such federal or state courts located in Texas', '', '', '', '', '', '', 'PERSON', '', 'NO', 'YES', 'Clark R. Moore', 'EVP', 'Viktor Tkachev', 'General Counsel', 1015.0, 'effective fifteen (15) days after Advisor s', 'YES', 'NO', 'NO', '21697_ADVISORY_AGREEMENT (3).doc_20210524_143234.txt', "Exhibit 10.14ADVISORY AGREEMENTThis Advisory Agreement is made and entered into, as of November 8, 2019 (“Effective Date”), by and between PEDEVCO Corp., a Texas corporation (“Company”), having a principal place of business at 575 N. Dairy Ashford, Energy Center II, Suite 210, Houston, Texas 77079 and Viktor T

D:\Users\Degananda.Reddy\AppData\Local\Temp\1/ipykernel_6528/3698195773.py:2: DeprecationWarning: The 'body' parameter is deprecated for the 'index' API and will be removed in a future version. Instead use the 'document' parameter. See https://github.com/elastic/elasticsearch-py/issues/1698 for more information
  res = es.index(index='k-nary', body=json_data)
D:\Users\Degananda.Reddy\Anaconda3\lib\site-packages\elasticsearch\connection\base.py:200: ElasticsearchWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.16/security-minimal-setup.html to enable security.
  warnings.warn(message, category=ElasticsearchWarning)


{'_index': 'k-nary', '_type': '_doc', '_id': 'es4Qvn0BSjNPN9g_1bY6', '_version': 1, 'result': 'created', '_shards': {'total': 2, 'successful': 1, 'failed': 0}, '_seq_no': 0, '_primary_term': 1}
[8731, 'NO', 'YES', 0, 'NO', datetime.datetime(2100, 1, 1, 0, 0), datetime.datetime(2100, 1, 1, 0, 0), 'Delaware', 'NO', 'Delaware', 'YES', 'NO', 'NO', '', 'CLM Matrix, a Texas corporation', '4808 Forest Hill Drive, Suite 2G Flower Mound, Texas 75028', '', '', 'Texas', 75028.0, '', 'Texas', 'Corp', '', '', 'Agrium U.S Inc.', '', '', '', '', '', '', 'Colorado', 'Corp', '', 'YES', 'YES', 'Timothy AGRIUM', 'CEO', 'Timothy B. Cabeootesti', '', 30.0, 'end of a written 30 day notice/cure period, if', 'YES', 'NO', 'YES', '21698_Agrium Nutrien Master Subscription Services Agreement executed 113018.pdf_20210524_143458.txt', ' Bi patriyMaster Subscription Services AgreementThis Master Subscription Services Agreement (“Agreement”) is between CLM Matrix, a Texas corporation (CLM) and Agrium U.S, Inc. aColor

{'_index': 'k-nary', '_type': '_doc', '_id': 'hs4Qvn0BSjNPN9g_1ra5', '_version': 1, 'result': 'created', '_shards': {'total': 2, 'successful': 1, 'failed': 0}, '_seq_no': 12, '_primary_term': 1}
[8754, 'NO', 'YES', 0, 'NO', Timestamp('2004-07-13 00:00:00+0000', tz='UTC'), datetime.datetime(2100, 1, 1, 0, 0), 'Tennessee', 'YES', '', 'NO', 'YES', 'NO', '501 Fifth Street, Bristol, Tennessee', 'King Pharmaceuticals, Inc.', '', '', '', '', '', 'Tennessee', 'Tennessee', 'Corp', '', '', 'Jefferson J. Gregory', '', '', '', '', '', '', '', 'PERSON', '', 'NO', 'YES', 'C. Diane', 'Vice President', 'Jefferson J. Gregory', '', '', '', 'NO', 'NO', 'NO', '21721_EX103__PRIVATE_AND_CONFIDENTIAL_____________________SEPARATION_AND_NONDISCLOSURE_AGREEMENT.doc_20210524_144350.txt', '<PAGE>EXHIBIT 10.3PRIVATE AND CONFIDENTIALSEPARATION AND NON-DISCLOSURE AGREEMENTTHIS AGREEMENT, dated the 13th day of July 2004, by and between KingPharmaceuticals, Inc., a Tennessee corporation, having its offices at 501 Fift

{'_index': 'k-nary', '_type': '_doc', '_id': 'jc4Qvn0BSjNPN9g_17bv', '_version': 1, 'result': 'created', '_shards': {'total': 2, 'successful': 1, 'failed': 0}, '_seq_no': 19, '_primary_term': 1}
[8768, 'NO', 'YES', 0, 'NO', Timestamp('2006-02-01 00:00:00+0000', tz='UTC'), datetime.datetime(2100, 1, 1, 0, 0), 'Florida', 'YES', 'Florida', 'NO', 'YES', 'NO', '6408 Parkland Drive, Suite 104, Sarasota, Florida 34243', 'Sun Energy Solar, Inc.', '', '', '', '', '', 'Florida', 'Delaware', 'Corp', '34243', '4819 Sky Blue Drive, Lutz, FL 33558', 'Robert Fugerer', '', '', '', '', '', 'FL', 'Florida', 'PERSON', '33558', 'NO', 'YES', 'Robert Fugerer', '', '', '', '', '', 'NO', 'NO', 'NO', '21735_NONDISCLOSURE_AGREEMENT_1842982.docx_20210524_145331.txt', 'Exhibit 10.6NON-DISCLOSURE AGREEMENTTHIS NON-DISCLOSURE AGREEMENT ("Agreement") is entered into this 2nd day of February, 2006 by and between Sun Energy Solar, Inc., a Delaware company having an address at 6408 Parkland Drive, Suite 104, Sarasota, 

...

{'_index': 'k-nary', '_type': '_doc', '_id': 'ec4Qvn0BSjNPN9g_-7fb', '_version': 1, 'result': 'created', '_shards': {'total': 2, 'successful': 1, 'failed': 0}, '_seq_no': 255, '_primary_term': 1}
[9297, 'YES', 'YES', 0, 'NO', Timestamp('2021-03-01 00:00:00+0000', tz='UTC'), datetime.datetime(2100, 1, 1, 0, 0), '', 'YES', '', 'NO', 'NO', 'NO', '', 'THE HENRY FILM AND ENTERTAINMENT CORPORATION', '', '', '', '', '', '', '', 'Other', '', '2809 Unicornio, Carlsbad, CA, 92009', '', '', '', '', '', '', 'CA,', '', '', '92009', 'YES', 'YES', 'Ed Litwak', 'Chairman', 'Date', 'Chairman', 30.0, 'within thirty (30) days following written', 'NO', 'NO', 'NO', '22241_PacificapEntertainmentHoldingsInc_20051115_8-KA_EX-1.01_4300894_EX-1.01_Content License Agreement.pdf_20210608_141616.txt', 'PACIFICAP ENTERTAINMENT Agreement with THE HENRY FILM AND ENTERTAINMENT CORPORATIONCONFIDENTIALPage 1 of 6CONTENT LICENSE AGREEMENTThis Content License Agreement is between THE HENRY FILM AND ENTERTAINMENT CORPORATI

{'_index': 'k-nary', '_type': '_doc', '_id': 'gc4Qvn0BSjNPN9g__LfA', '_version': 1, 'result': 'created', '_shards': {'total': 2, 'successful': 1, 'failed': 0}, '_seq_no': 263, '_primary_term': 1}
[9312, 'NO', 'NO', 0, 'NO', Timestamp('2012-02-20 00:00:00+0000', tz='UTC'), datetime.datetime(2100, 1, 1, 0, 0), 'Georgia', 'YES', '', 'NO', 'NO', 'NO', '', 'Healthcare Distribution Specialists LLC', '', '', '', '', '', '', 'Delaware', 'LLC', '', " HDS' product, Clotamin in the United States", '', '', '', '', '', '', '', '', '', '', 'NO', 'YES', 'Linda Lee', 'Distribution Specialist', 'Mackie A.', 'CEO', 101077103.0, 'upon ten (10) days prior written notice', 'YES', 'NO', 'YES', '22256_PharmagenInc_20120803_8-KA_EX-10.1_7693204_EX-10.1_Endorsement Agreement.pdf_20210608_142343.txt', 'Exhibit 10.1 ENDORSEMENT AGREEMENT  THIS ENDORSEMENT AGREEMENT (the "Agreement") is dated as of this ____day of ____________, 2012, but made effective as of February 20, 2012 ("Effective Date") between Healthcare

{'_index': 'k-nary', '_type': '_doc', '_id': 'h84Qvn0BSjNPN9g__bfH', '_version': 1, 'result': 'created', '_shards': {'total': 2, 'successful': 1, 'failed': 0}, '_seq_no': 269, '_primary_term': 1}
[9324, 'NO', 'YES', 0, 'NO', Timestamp('2000-11-14 00:00:00+0000', tz='UTC'), datetime.datetime(2100, 1, 1, 0, 0), 'New York', 'YES', 'New York', 'NO', 'YES', 'NO', '', 'Dassault Systemes', '2520 55th Street, Suite 200 Boulder, Colorado 80301', '', '', 'Colorado', 80301.0, '', '', 'Other', '', '', 'Dassault Systemes', '2520 55th Street, Suite 200  Boulder, Colorado 80301', '', '', 'Colorado', 80301.0, '', '', 'Other', '', 'YES', 'YES', 'Dassault Systemes', 'Chief Executive Officer', 'R. Bruce Morgan', 'Executive Vice President', 1095365180.0, 'in force for three years from the Launch', 'YES', 'YES', 'YES', '22268_RandWorldwideInc_20010402_8-KA_EX-10.2_2102464_EX-10.2_Co-Branding Agreement.pdf_20210608_143457.txt', '   1                                                                    EXHIBIT

{'_index': 'k-nary', '_type': '_doc', '_id': 'jc4Qvn0BSjNPN9g__rfT', '_version': 1, 'result': 'created', '_shards': {'total': 2, 'successful': 1, 'failed': 0}, '_seq_no': 275, '_primary_term': 1}
[9331, 'YES', 'YES', 3600, 'NO', Timestamp('2020-02-04 00:00:00+0000', tz='UTC'), datetime.datetime(2100, 1, 1, 0, 0), '', 'YES', 'Illinois', 'NO', 'YES', 'NO', '', 'Reynolds Group Holdings Inc.', '1900 W. Field Court Lake Forest, IL 60045', '', '', 'IL', 60045.0, '', 'Delaware', 'Corp', '', '', 'Reynolds Consumer Products Inc.', '', '', '', '', '', '', 'Delaware', 'Corp', '', 'YES', 'NO', '', '', '', '', 606030.0, 'within thirty (30) days of written notice', 'NO', 'YES', 'NO', '22275_ReynoldsConsumerProductsInc_20200121_S-1A_EX-10.22_11948918_EX-10.22_Service Agreement.pdf_20210608_144904.txt', 'Exhibit 10.22TRANSITION SERVICES AGREEMENTTRANSITION SERVICES AGREEMENT (the “Agreement”) dated as of [•], 2020, between Reynolds Group Holdings Inc., a Delaware corporation(“RGHI”), and Reynolds Cons

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [6]:
print(es.indices.get_alias("*"))

{'my-index': {'aliases': {}}, 'k-nary': {'aliases': {}}, 'test-index2': {'aliases': {}}, 'test-index': {'aliases': {}}}


D:\Users\Degananda.Reddy\AppData\Local\Temp\1/ipykernel_6528/504408242.py:1: DeprecationWarning: Using positional arguments for APIs is deprecated and will be disabled in 8.0.0. Instead use only keyword arguments for all APIs. See https://github.com/elastic/elasticsearch-py/issues/1698 for more information
  print(es.indices.get_alias("*"))


In [70]:
print(es.count(index="k-nary")) 

{'count': 304, '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0}}


In [ ]:
#query = Q('range', Expiration_Date={'gte': datetime.datetime(2021, 12, 31)})

In [85]:
s = Search(using=es, index='k-nary')
s = s.query('match', text_content='Janus')
res = s.execute()

In [170]:
def search(expiry_in_days,contract_party,adrt):
    s = Search(using=es, index='k-nary')
    if expiry_in_days!="":
        Date_req = date.today() + timedelta(days=expiry_in_days)
        s=s.query(Q('range', Expiration_Date={"gte": "now","lte":Date_req}))
    else:
        pass
    if contract_party!="":
        s=s.filter('multi_match', query=contract_party ,fields=['Party_1_Name', 'Party_2_Name'],minimum_should_match="100%")
    else:
        pass
    if adrt!="":
        s=s.filter("match",Alternate_Dispute_Resolution_Terms=adrt)
    else:
        pass
    s=s[0:s.count()]
    response = s.execute()
    total_contracts=s.count()
    df=pd.DataFrame(columns=['contract_id','contract_party1','contract_party2','Expiration_date','Alternate_Dispute_Resolution_Terms'])
    for hit in response:
        contract_id=hit.contract_id
        #filename=hit.file_name
        contract_party1=hit.Party_1_Name
        contract_party2=hit.Party_2_Name
        expirydate=hit.Expiration_Date
        Alternate_Dispute_Resolution_Terms=hit.Alternate_Dispute_Resolution_Terms
        df.loc[len(df)]=[contract_id,contract_party1,contract_party2,expirydate,Alternate_Dispute_Resolution_Terms]
    return df,total_contracts

In [172]:
df,total_contracts=search("","","yes")
print("total_contracts:",total_contracts)
df

D:\Users\Degananda.Reddy\Anaconda3\lib\site-packages\elasticsearch\connection\base.py:200: ElasticsearchWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.16/security-minimal-setup.html to enable security.
  warnings.warn(message, category=ElasticsearchWarning)


total_contracts: 102


contract_id                contract_party1  \
0          8742      Vyera Pharmaceuticals LLC   
1          8748  United Launch Alliance L.L.C.   
2          8753                    PFENEX INC.   
3          8756         GE PACKAGED POWER INC.   
4          8759             Lexaria Hemp Corp.   
..          ...                            ...   
97         9374    ExxonMobil Chemical Company   
98         9376                 Calm.com, Inc.   
99         9377                   ZOGENIX INC.   
100      111111                    ABC Company   
101      111113                   ABC2 Company   

                       contract_party2            Expiration_date  \
0                         CytoDyn Inc.        2100-01-01T00:00:00   
1       The Boeing Company corporation  2021-03-31T00:00:00+00:00   
2                    ALVOGEN MALTA LTD        2100-01-01T00:00:00   
3                     MMC Energy, Inc.        2100-01-01T00:00:00   
4    Hill Street Beverage Company Inc.        2100-01-01T00:00:00   
..                                 ...                        ...   
97                          ExxonMobil        2100-01-01T00:00:00   
98                XpresSpa Group, Inc.  2019-07-31T00:00:00+00:00   
99       Nippon Shinyaku Company, Ltd.        2100-01-01T00:00:00   
100                        XYZ Company  2021-12-31T00:00:00+00:00   
101                       XYZ2 Company  2022-03-01T00:00:00+00:00   

    Alternate_Dispute_Resolution_Terms  
0                                  YES  
1                                  YES  
2                                  YES  
3                                  YES  
4                                  YES  
..                                 ...  
97                                 YES  
98                                 YES  
99                                 YES  
100                                YES  
101                                YES  

[102 rows x 5 columns]

In [137]:
s = s.filter("match",Alternate_Dispute_Resolution_Terms=alternate_dispute_resolution_terms).filter('multi_match', query=contract_party_name ,fields=['Party_1_Name', 'Party_2_Name'],minimum_should_match="100%").query(Q('range', Expiration_Date={"gte": "now","lte":Date_req}))


10

In [146]:
s = Search(using=es, index='k-nary')
#s=s[0:s.count()]
response = s.execute()
print("Total contracts:",s.count())
for hit in response:
    print(hit.Party_1_Name,hit.contract_id)

Total contracts: 304
PEDEVCO Corp. 8730
CLM Matrix, a Texas corporation 8731
Rhodia Inc., a Delaware corporation 8734
CLM Matrix, a Texas corporation 8735
11030 Roselle Street 8738
Vyera Pharmaceuticals LLC 8742
The Dayton Power 8743
CPS HR Consulting 8746
United Launch Alliance L.L.C. 8748
Taronis Technologies, Inc. 8749


In [145]:
s = Search(using=es, index='k-nary')
query = Q('match', Alternate_Dispute_Resolution_Terms='yes')      
s = s.query(query)
#s=s[0:s.count()]
response = s.execute()
print("Total contracts:",s.count())
for hit in response:
    print(hit.Party_1_Name,hit.contract_id)

Total contracts: 102
Vyera Pharmaceuticals LLC 8742
United Launch Alliance L.L.C. 8748
PFENEX INC. 8753
GE PACKAGED POWER INC. 8756
Lexaria Hemp Corp. 8759
Aptose Biosciences Inc. 8774
Farmers & Merchants Bank of Central California 8778
Innerwall, Inc. 8784
Innerwall, Inc. 8797
Innerwall, Inc. 8806


In [115]:
#query = Q('match', Party_1_Name={"query":"PhaseBio Pharmaceuticals ","minimum_should_match": "100%"})
query =Q('multi_match', query="PhaseBio Pharmaceuticals inc" ,fields=['Party_1_Name', 'Party_2_Name'],minimum_should_match="100%")
s = Search(using=es, index='k-nary').query(query)
response = s.execute()
print("Total contracts:",s.count())
for hit in response:
    print(hit.Party_1_Name,hit.contract_id)

Total contracts: 2
PhaseBio Pharmaceuticals Inc. 9061
PhaseBio Pharmaceuticals Inc. 9313


In [131]:
s = Search(using=es, index='k-nary')
Date_req = date.today() + timedelta(days=365)
s = s.filter('multi_match', query="" ,fields=['Party_1_Name', 'Party_2_Name'],minimum_should_match="100%").query(Q('range', Expiration_Date={"gte": "now","lte":Date_req}))  

response = s.execute()
print("Total contracts:",s.count())
for hit in response:
    print(hit.Party_1_Name,hit.contract_id)

TypeError: __init__() got an unexpected keyword argument 'size'

In [ ]:
def contractsBasedOnExpiry(no_of_days):
    Date_req = date.today() + timedelta(days=no_of_days)
    query = Q('range', Expiration_Date={"gte": "now","lte":Date_req})
    s = Search(using=es, index='k-nary').query(query)
    response = s.execute()
    print("Total contracts:",s.count())
    for hit in response:
        print(hit.Party_1_Name,hit.contract_id)

In [ ]:
contractsBasedOnExpiry(60)

In [101]:
def contractsBasedOnNameAndExpiry(party_name,no_of_days):
    Date_req = date.today() + timedelta(days=no_of_days)
    query = Q('multi_match', query=party_name,fields=['Party_1_Name', 'Party_2_Name'],minimum_should_match="100%") & Q('range', Expiration_Date={"gte": "now","lte":Date_req})
    s = Search(using=es, index='k-nary').query(query)
    response = s.execute()
    for hit in response:
        if hit.Party_1_Name==party_name or hit.Party_2_Name==party_name:
            print(hit.Party_1_Name,hit.contract_id)

In [108]:
contractsBasedOnNameAndExpiry("VerticalNet",90)

In [43]:
def searchbyAll(no_of_days='',contract_party_name='',alternate_dispute_resolution_terms=''):
    print(no_of_days)
    print(contract_party_name)
    print(str(alternate_dispute_resolution_terms))
    s = Search(using=es, index='k-nary')
    if (no_of_days!="" and (contract_party_name=="" and alternate_dispute_resolution_terms=='')):
        print(1)
        Date_req = date.today() + timedelta(days=no_of_days)
        query = Q('range', Expiration_Date={"gte": "now","lte":Date_req})
        s = s.query(query)
    elif contract_party_name!="" and (no_of_days=="" and alternate_dispute_resolution_terms==''):
        print(2)
        query = Q('multi_match', query=contract_party_name,fields=['Party_1_Name', 'Party_2_Name'])
        s = s.query(query)
    elif alternate_dispute_resolution_terms!="" and (no_of_days=="" and contract_party_name==''):
        print(3)
        query = Q('match', Alternate_Dispute_Resolution_Terms=alternate_dispute_resolution_terms)      
        s = s.query(query)
        
    elif (no_of_days!="" and contract_party_name!='') and alternate_dispute_resolution_terms=='':
        print(4)
        Date_req = date.today() + timedelta(days=no_of_days)
        s = s.filter("match", Party_1_Name=contract_party_name).query(Q('range', Expiration_Date={"gte": "now","lte":Date_req}))  

    elif (alternate_dispute_resolution_terms!="" and contract_party_name!='') and no_of_days=='':
        print(5)
        s = s.filter("match", Alternate_Dispute_Resolution_Terms=alternate_dispute_resolution_terms).query(Q('match', Party_1_Name=contract_party_name))

    elif (alternate_dispute_resolution_terms!="" and no_of_days!='') and contract_party_name=='':
        print(6)
        Date_req = date.today() + timedelta(days=no_of_days)
        s = s.filter("match", Alternate_Dispute_Resolution_Terms=alternate_dispute_resolution_terms).query(Q('range', Expiration_Date={"gte": "now","lte":Date_req}))

    else:
        Date_req = date.today() + timedelta(days=no_of_days)
        s = s.filter("match",Alternate_Dispute_Resolution_Terms=alternate_dispute_resolution_terms).filter("match", Party_1_Name=contract_party_name).query(Q('range', Expiration_Date={"gte": "now","lte":Date_req}))

    response = s.execute()
    total_contracts=s.count()
    df=pd.DataFrame(columns=['contract_id','filename','contract_partyname','Expiration_date','Alternate_Dispute_Resolution_Terms'])
    for hit in response:
        contract_id=hit.contract_id
        filename=hit.file_name
        contract_party=hit.Party_1_Name
        expirydate=hit.Expiration_Date
        Alternate_Dispute_Resolution_Terms=hit.Alternate_Dispute_Resolution_Terms
        df.loc[len(df)]=[contract_id,filename,contract_party,expirydate,Alternate_Dispute_Resolution_Terms]
    return df,total_contracts

In [28]:
s = Search(using=es, index='k-nary')
Date_req = date.today() + timedelta(days=90)
s = s.filter("match", Alternate_Dispute_Resolution_Terms="YES").query(Q('range', Expiration_Date={"gte": "now","lte":Date_req}))
response = s.execute()
df=pd.DataFrame(columns=['contract_id','filename','contract_partyname','Expiration_date','Alternate_Dispute_Resolution_Terms'])
for hit in response:
    contract_id=hit.contract_id
    filename=hit.file_name
    contract_party=hit.Party_1_Name
    expirydate=hit.Expiration_Date
    Alternate_Dispute_Resolution_Terms=hit.Alternate_Dispute_Resolution_Terms
    df.loc[len(df)]=[contract_id,filename,contract_party,expirydate,Alternate_Dispute_Resolution_Terms]
df

D:\Users\Degananda.Reddy\Anaconda3\lib\site-packages\elasticsearch\connection\base.py:200: ElasticsearchWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.16/security-minimal-setup.html to enable security.
  warnings.warn(message, category=ElasticsearchWarning)


contract_id          filename contract_partyname            Expiration_date  \
0      111111  Sample_file1.txt        ABC Company  2021-12-31T00:00:00+00:00   
1      111113  Sample_file3.txt       ABC2 Company  2022-03-01T00:00:00+00:00   

  Alternate_Dispute_Resolution_Terms  
0                                YES  
1                                YES

In [63]:

searchbyAll(90,'abc1','NO')

90
abc1
NO


D:\Users\Degananda.Reddy\Anaconda3\lib\site-packages\elasticsearch\connection\base.py:200: ElasticsearchWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.16/security-minimal-setup.html to enable security.
  warnings.warn(message, category=ElasticsearchWarning)


(  contract_id          filename contract_partyname            Expiration_date  \
 0      111112  Sample_file2.txt       ABC1 Company  2022-01-31T00:00:00+00:00   
 
   Alternate_Dispute_Resolution_Terms  
 0                                 NO  ,
 1)

In [ ]:
def search(no_of_days,contract_party_name=''):
    try: 
        Date_req = date.today() + timedelta(days=no_of_days)
    except Exception as TypeError:
        print()
    s = Search(using=es, index='k-nary')
    if contract_party_name=="":
        query = Q('range', Expiration_Date={"gte": "now","lte":Date_req})
        s = s.query(query)
    elif no_of_days=='':
        query = Q('multi_match', query=contract_party_name,fields=['Party_1_Name', 'Party_2_Name'])
        s = s.query(query)
    else:
        s = s.filter("range", Expiration_Date={"gte": "now", "lt": Date_req}).query(Q('multi_match', query=contract_party_name,fields=['Party_1_Name', 'Party_2_Name']))
    response = s.execute()
    total_contracts=s.count()
    df=pd.DataFrame(columns=['contract_id','filename','contract_partyname','Expiration_date'])
    for hit in response:
        contract_id=hit.contract_id
        filename=hit.file_name
        contract_party=hit.Party_1_Name
        expirydate=hit.Expiration_Date
        df.loc[len(df)]=[contract_id,filename,contract_party,expirydate]
    return df,total_contracts
        

In [ ]:
search('','abc2')

In [ ]:
json_data

In [ ]:
contractsBasedOnExpiry(90)

In [ ]:
contractsBasedOnNameAndExpiry("ABC2 Company",90)

In [ ]:
q = Q("multi_match", query='python django', fields=['title', 'body'])

In [ ]:
for hit in response:
    print(hit.Party_1_Name,hit.contract_id)

In [ ]:
json_data

In [ ]:
Date_req = date.today() + timedelta(days=17)

In [ ]:
Date_req

In [ ]:
req_date = date.today() + pd.DateOffset(days=3)

In [ ]:
req_date

In [169]:
# back up for first version
def searchbyAll(no_of_days='',contract_party_name='',alternate_dispute_resolution_terms=''):
    s = Search(using=es,index='k-nary')
    if no_of_days!="" and (contract_party_name=='' and alternate_dispute_resolution_terms==''):
        Date_req = date.today() + timedelta(days=no_of_days)
        query = Q('range', Expiration_Date={"gte": "now","lte":Date_req})
        s = s.query(query)
    elif contract_party_name!="" and (no_of_days=='' and alternate_dispute_resolution_terms==''):
        query = Q('multi_match', query=contract_party_name,fields=['Party_1_Name', 'Party_2_Name'],minimum_should_match="100%")
        s = s.query(query)
    elif alternate_dispute_resolution_terms!="" and (no_of_days=='' and contract_party_name==''):
        query = Q('match', Alternate_Dispute_Resolution_Terms=alternate_dispute_resolution_terms)      
        s = s.query(query)
        
    elif (no_of_days!='' and contract_party_name!='') and alternate_dispute_resolution_terms=='':
        Date_req = date.today() + timedelta(days=no_of_days)
        s = s.filter('multi_match', query=contract_party_name ,fields=['Party_1_Name', 'Party_2_Name'],minimum_should_match="100%").query(Q('range', Expiration_Date={"gte": "now","lte":Date_req}))  
    elif (alternate_dispute_resolution_terms!='' and contract_party_name!='') and no_of_days=='':
        s = s.filter("match", Alternate_Dispute_Resolution_Terms=alternate_dispute_resolution_terms).query(Q('multi_match', query=contract_party_name,fields=['Party_1_Name', 'Party_2_Name'],minimum_should_match="100%"))
    elif (alternate_dispute_resolution_terms!='' and no_of_days!='') and contract_party_name=='':
        Date_req = date.today() + timedelta(days=no_of_days)
        s = s.filter("match", Alternate_Dispute_Resolution_Terms=alternate_dispute_resolution_terms).query(Q('range', Expiration_Date={"gte": "now","lte":Date_req}))

    else:
        Date_req = date.today() + timedelta(days=no_of_days)
        s = s.filter("match",Alternate_Dispute_Resolution_Terms=alternate_dispute_resolution_terms).filter('multi_match', query=contract_party_name ,fields=['Party_1_Name', 'Party_2_Name'],minimum_should_match="100%").query(Q('range', Expiration_Date={"gte": "now","lte":Date_req}))
    s=s[0:s.count()]
    response = s.execute()
    total_contracts=s.count()
    df=pd.DataFrame(columns=['contract_id','contract_party1','contract_party2','Expiration_date','Alternate_Dispute_Resolution_Terms'])
    for hit in response:
        contract_id=hit.contract_id
        #filename=hit.file_name
        contract_party1=hit.Party_1_Name
        contract_party2=hit.Party_2_Name
        expirydate=hit.Expiration_Date
        Alternate_Dispute_Resolution_Terms=hit.Alternate_Dispute_Resolution_Terms
        df.loc[len(df)]=[contract_id,contract_party1,contract_party2,expirydate,Alternate_Dispute_Resolution_Terms]
    return df,total_contracts